In [12]:
import sqlite3
import pandas as pd
import sweetviz as sv

#step 1: Bring in the data from SQLite

#connect to the database
conn = sqlite3.connect('tuition.db')
try:
    print("✅ Connection successful.")
except sqlite3.Error as e:
    print("❌ Connection failed:", e)

#see what tables are available in the db
tables = pd.read_sql_query("SELECT name FROM sqlite_master WHERE type='table';", conn)
print(tables)

#when 0 tuition is shown, that means there is one table.
#load data
tuitiondf = pd.read_sql_query("SELECT * FROM tuition", conn)
tuitiondf.head()


✅ Connection successful.
      name
0  tuition


Sector_Name Unit_ID   OPEID                            Institution_Name  \
0  4-year, public  231624  370500                              William & Mary   
1  4-year, public  216339  337100                           Temple University   
2  4-year, public  215293  337900  University of Pittsburgh-Pittsburgh Campus   
3  4-year, public  234076  374500          University of Virginia-Main Campus   
4  4-year, public  126775  134800                    Colorado School of Mines   

  State 22/23_Tuition  
0    VA        23,970  
1    PA        21,135  
2    PA        21,080  
3    VA        20,342  
4    CO        20,040

In [14]:
#Basic Profile data
tuitiondf.info()
tuitiondf.describe(include='all')  # Includes numerical, categorical, etc.
tuitiondf.isnull().sum()           # Check missing values
tuitiondf.nunique()                # Unique values per column



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 6 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Sector_Name       3419 non-null   object
 1   Unit_ID           3419 non-null   object
 2   OPEID             3419 non-null   object
 3   Institution_Name  3419 non-null   object
 4   State             3419 non-null   object
 5   22/23_Tuition     3419 non-null   object
dtypes: object(6)
memory usage: 160.4+ KB


Sector_Name            9
Unit_ID             3419
OPEID               3403
Institution_Name    3378
State                 59
22/23_Tuition       2744
dtype: int64

In [18]:
#compare the basic to the ydata-profiling
from ydata_profiling import ProfileReport

tuitionprofile = ProfileReport(tuitiondf, title="Tuition Data Profile", explorative=True)
tuitionprofile.to_notebook_iframe()  # Display in Jupyter Notebook


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
#convert data types
'''
Examples on how to convert:
df["Name"] = df["Name"].astype("string")
df["Date"] = pd.to_datetime(df["Date"])
df["Price"] = pd.to_numeric(df["Price"], errors='coerce')
'''
'''

Reference for the tuition db
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Sector_Name       3419 non-null   object
 1   Unit_ID           3419 non-null   object
 2   OPEID             3419 non-null   object
 3   Institution_Name  3419 non-null   object
 4   State             3419 non-null   object
 5   22/23_Tuition     3419 non-null   object

 Sector_Name	Unit_ID	OPEID	Institution_Name	State	22/23_Tuition
 4-year, public	231624	370500	William & Mary	      VA	23,970

Sector_Name
'''
#Before fixing data type, I need to split the sector name column because it's actually two data items that will have their own data types

# Split into two new columns
tuitiondf[['Degree_Length', 'Ownership']] = tuitiondf['Sector_Name'].str.split(',', expand=True)

# Optional: clean up spaces
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].str.strip()
tuitiondf['Ownership'] = tuitiondf['Ownership'].str.strip()
'''



In [22]:
# Split the column
tuitiondf[['Degree_Length', 'Ownership']] = tuitiondf['Sector_Name'].str.split(',', expand=True)

# Clean up whitespace
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].str.strip()
tuitiondf['Ownership'] = tuitiondf['Ownership'].str.strip()

# Enforce original data types
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].astype('object')  # Legacy string type
tuitiondf['Ownership'] = tuitiondf['Ownership'].astype('string')          # Newer pandas string type


In [24]:
tuitiondf.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Sector_Name       3419 non-null   object
 1   Unit_ID           3419 non-null   object
 2   OPEID             3419 non-null   object
 3   Institution_Name  3419 non-null   object
 4   State             3419 non-null   object
 5   22/23_Tuition     3419 non-null   object
 6   Degree_Length     3419 non-null   object
 7   Ownership         3419 non-null   string
dtypes: object(7), string(1)
memory usage: 213.8+ KB


In [26]:
tuitiondf.head()

Sector_Name Unit_ID   OPEID                            Institution_Name  \
0  4-year, public  231624  370500                              William & Mary   
1  4-year, public  216339  337100                           Temple University   
2  4-year, public  215293  337900  University of Pittsburgh-Pittsburgh Campus   
3  4-year, public  234076  374500          University of Virginia-Main Campus   
4  4-year, public  126775  134800                    Colorado School of Mines   

  State 22/23_Tuition Degree_Length Ownership  
0    VA        23,970        4-year    public  
1    PA        21,135        4-year    public  
2    PA        21,080        4-year    public  
3    VA        20,342        4-year    public  
4    CO        20,040        4-year    public

In [ ]:
tuitiondf = tuitiondf.drop(columns=['Sector_Name'])

In [32]:
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0  231624  370500                              William & Mary    VA   
1  216339  337100                           Temple University    PA   
2  215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3  234076  374500          University of Virginia-Main Campus    VA   
4  126775  134800                    Colorado School of Mines    CO   

  22/23_Tuition Degree_Length Ownership  
0        23,970        4-year    public  
1        21,135        4-year    public  
2        21,080        4-year    public  
3        20,342        4-year    public  
4        20,040        4-year    public

In [34]:
#automatically converts data types based on what pandas infers 
tuitiondf = tuitiondf.convert_dtypes()
tuitiondf.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Unit_ID           3419 non-null   string
 1   OPEID             3419 non-null   string
 2   Institution_Name  3419 non-null   string
 3   State             3419 non-null   string
 4   22/23_Tuition     3419 non-null   object
 5   Degree_Length     3419 non-null   string
 6   Ownership         3419 non-null   string
dtypes: object(1), string(6)
memory usage: 187.1+ KB


In [36]:
#the above was incorrect so need to do this manually

# Convert to numeric (will convert invalid to NaN)
tuitiondf['Unit_ID'] = pd.to_numeric(tuitiondf['Unit_ID'], errors='coerce')
tuitiondf['OPEID'] = pd.to_numeric(tuitiondf['OPEID'], errors='coerce')
tuitiondf['22/23_Tuition'] = pd.to_numeric(tuitiondf['22/23_Tuition'], errors='coerce')


In [38]:
tuitiondf.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Unit_ID           3419 non-null   Int64  
 1   OPEID             3419 non-null   Int64  
 2   Institution_Name  3419 non-null   string 
 3   State             3419 non-null   string 
 4   22/23_Tuition     3 non-null      float64
 5   Degree_Length     3419 non-null   string 
 6   Ownership         3419 non-null   string 
dtypes: Int64(2), float64(1), string(4)
memory usage: 193.8 KB


In [48]:
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

  22/23_Tuition Degree_Length Ownership  
0          $nan        4-year    public  
1          $nan        4-year    public  
2          $nan        4-year    public  
3          $nan        4-year    public  
4          $nan        4-year    public

In [50]:
tuitiondf['22/23_Tuition'] = (
    tuitiondf['22/23_Tuition']
    .replace('[\$,]', '', regex=True)
    .astype(float)
)
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

   22/23_Tuition Degree_Length Ownership  
0            NaN        4-year    public  
1            NaN        4-year    public  
2            NaN        4-year    public  
3            NaN        4-year    public  
4            NaN        4-year    public

In [52]:
tuitiondf['22/23_Tuition'] = pd.to_numeric(tuitiondf['22/23_Tuition'], errors='coerce')
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

   22/23_Tuition Degree_Length Ownership  
0            NaN        4-year    public  
1            NaN        4-year    public  
2            NaN        4-year    public  
3            NaN        4-year    public  
4            NaN        4-year    public

In [54]:
tuitiondf = tuitiondf.convert_dtypes('22/23_Tuition')
tuitiondf.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Unit_ID           3419 non-null   Int64 
 1   OPEID             3419 non-null   Int64 
 2   Institution_Name  3419 non-null   string
 3   State             3419 non-null   string
 4   22/23_Tuition     3 non-null      Int64 
 5   Degree_Length     3419 non-null   string
 6   Ownership         3419 non-null   string
dtypes: Int64(3), string(4)
memory usage: 197.1 KB


In [56]:
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

   22/23_Tuition Degree_Length Ownership  
0           <NA>        4-year    public  
1           <NA>        4-year    public  
2           <NA>        4-year    public  
3           <NA>        4-year    public  
4           <NA>        4-year    public

In [60]:
tuitiondf['22/23_Tuition'] = tuitiondf['22/23_Tuition'].astype('object')
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

  22/23_Tuition Degree_Length Ownership  
0          <NA>        4-year    public  
1          <NA>        4-year    public  
2          <NA>        4-year    public  
3          <NA>        4-year    public  
4          <NA>        4-year    public

In [62]:
# Undo currency formatting
tuitiondf['22/23_Tuition'] = pd.to_numeric(
    tuitiondf['22/23_Tuition'].replace('[\$,]', '', regex=True),
    errors='coerce'
)


In [64]:
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

   22/23_Tuition Degree_Length Ownership  
0            NaN        4-year    public  
1            NaN        4-year    public  
2            NaN        4-year    public  
3            NaN        4-year    public  
4            NaN        4-year    public

In [66]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('tuition.db')
tuitiondf = pd.read_sql_query("SELECT * FROM tuition", conn)
print("Successful")


Successful


In [70]:
tuitiondf.head()

Sector_Name Unit_ID   OPEID                            Institution_Name  \
0  4-year, public  231624  370500                              William & Mary   
1  4-year, public  216339  337100                           Temple University   
2  4-year, public  215293  337900  University of Pittsburgh-Pittsburgh Campus   
3  4-year, public  234076  374500          University of Virginia-Main Campus   
4  4-year, public  126775  134800                    Colorado School of Mines   

  State 22/23_Tuition  
0    VA        23,970  
1    PA        21,135  
2    PA        21,080  
3    VA        20,342  
4    CO        20,040

In [72]:
# Split the Sector_Name column
tuitiondf[['Degree_Length', 'Ownership']] = tuitiondf['Sector_Name'].str.split(',', expand=True)

# Clean up whitespace
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].str.strip()
tuitiondf['Ownership'] = tuitiondf['Ownership'].str.strip()

# Enforce original data types
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].astype('object')  # Legacy string type
tuitiondf['Ownership'] = tuitiondf['Ownership'].astype('string')          # Newer pandas string type

tuitiondf.head()

Sector_Name Unit_ID   OPEID                            Institution_Name  \
0  4-year, public  231624  370500                              William & Mary   
1  4-year, public  216339  337100                           Temple University   
2  4-year, public  215293  337900  University of Pittsburgh-Pittsburgh Campus   
3  4-year, public  234076  374500          University of Virginia-Main Campus   
4  4-year, public  126775  134800                    Colorado School of Mines   

  State 22/23_Tuition Degree_Length Ownership  
0    VA        23,970        4-year    public  
1    PA        21,135        4-year    public  
2    PA        21,080        4-year    public  
3    VA        20,342        4-year    public  
4    CO        20,040        4-year    public

In [74]:
tuitiondf = tuitiondf.drop(columns=['Sector_Name'])
print("Success!")

Success!


In [80]:
# Convert to numeric (will convert invalid to NaN)
tuitiondf['Unit_ID'] = pd.to_numeric(tuitiondf['Unit_ID'], errors='coerce')
tuitiondf['OPEID'] = pd.to_numeric(tuitiondf['OPEID'], errors='coerce')

tuitiondf.info()
tuitiondf.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Unit_ID           3419 non-null   int64  
 1   OPEID             3419 non-null   int64  
 2   Institution_Name  3419 non-null   string 
 3   State             3419 non-null   object 
 4   22/23_Tuition     3 non-null      float64
 5   Degree_Length     3419 non-null   object 
 6   Ownership         3419 non-null   string 
dtypes: float64(1), int64(2), object(2), string(2)
memory usage: 187.1+ KB


Unit_ID   OPEID                            Institution_Name State  \
0   231624  370500                              William & Mary    VA   
1   216339  337100                           Temple University    PA   
2   215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3   234076  374500          University of Virginia-Main Campus    VA   
4   126775  134800                    Colorado School of Mines    CO   

   22/23_Tuition Degree_Length Ownership  
0            NaN        4-year    public  
1            NaN        4-year    public  
2            NaN        4-year    public  
3            NaN        4-year    public  
4            NaN        4-year    public

In [78]:
tuitiondf['Institution_Name'] = tuitiondf['Institution_Name'].astype('string')
print("Success 🎉")


Success 🎉


<div style="background-color: #ff46a2; padding: 10px; border-radius: 5px; border: 1px solid #ffeeba;">
  <strong>Note: The above is where mistakes were made. The below is clean. </strong>
</div>


<div style="background-color: #f5f5f5; padding: 10px; border-radius: 5px; border: 3px solid #ff46A2;">
  <strong> Tuition </strong>
</div>


In [84]:
#load the data
conn = sqlite3.connect('tuition.db')
tuitiondf = pd.read_sql_query("SELECT * FROM tuition", conn)

# Split the Sector_Name column
tuitiondf[['Degree_Length', 'Ownership']] = tuitiondf['Sector_Name'].str.split(',', expand=True)

# Clean up whitespace
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].str.strip()
tuitiondf['Ownership'] = tuitiondf['Ownership'].str.strip()

# Enforce original data types
tuitiondf['Degree_Length'] = tuitiondf['Degree_Length'].astype('object')  # Legacy string type
tuitiondf['Ownership'] = tuitiondf['Ownership'].astype('string')          # Newer pandas string type

# Drop the original column
tuitiondf = tuitiondf.drop(columns=['Sector_Name'])

# Show changes so far
tuitiondf.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3419 entries, 0 to 3418
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Unit_ID           3419 non-null   object
 1   OPEID             3419 non-null   object
 2   Institution_Name  3419 non-null   object
 3   State             3419 non-null   object
 4   22/23_Tuition     3419 non-null   object
 5   Degree_Length     3419 non-null   object
 6   Ownership         3419 non-null   string
dtypes: object(6), string(1)
memory usage: 187.1+ KB


In [86]:
tuitiondf.head()

Unit_ID   OPEID                            Institution_Name State  \
0  231624  370500                              William & Mary    VA   
1  216339  337100                           Temple University    PA   
2  215293  337900  University of Pittsburgh-Pittsburgh Campus    PA   
3  234076  374500          University of Virginia-Main Campus    VA   
4  126775  134800                    Colorado School of Mines    CO   

  22/23_Tuition Degree_Length Ownership  
0        23,970        4-year    public  
1        21,135        4-year    public  
2        21,080        4-year    public  
3        20,342        4-year    public  
4        20,040        4-year    public

In [ ]:
'''
import os
Purpose: Imports Python’s built-in os module, which allows interaction with the operating system—like reading directory contents.
Why it's needed: So we can use os.listdir() to get the list of files in a folder.
os.listdir('.')
Returns: A list of all files and folders in the current working directory (indicated by the dot '.').
Example output: ['tuition.db', 'notes.txt', 'data.sqlite', 'script.py']
[f for f in os.listdir('.') if f.endswith(('.db', '.sqlite'))]
What it is: A list comprehension that filters only the files ending in .db or .sqlite.
How it works:
f for f in os.listdir('.') → loops over each file f
if f.endswith(('.db', '.sqlite')) → keeps only files that end in .db or .sqlite
Result: A list like ['tuition.db', 'schools.sqlite']
'''

In [ ]:
<div style="background-color: #f5f5f5; padding: 10px; border-radius: 5px; border: 3px solid #ff46A2;">
  <strong> Study Areas </strong>
</div>

<div style="background-color: #f5f5f5; padding: 10px; border-radius: 5px; border: 3px solid #ff46A2;">
  <strong> Study Areas </strong>
</div>

In [112]:
#load the STUDYAREAS data
conn = sqlite3.connect('studyareas.db')
studyareasdf = pd.read_sql_query("SELECT * FROM studyareas", conn)

studyareasdf.info()
studyareasdf.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 229188 entries, 0 to 229187
Data columns (total 6 columns):
 #   Column    Non-Null Count   Dtype  
---  ------    --------------   -----  
 0   UNITID    229188 non-null  object 
 1   OPEID6    229188 non-null  float64
 2   INSTNM    229188 non-null  object 
 3   CIPCODE   229188 non-null  float64
 4   CREDLEV   229188 non-null  int64  
 5   CREDDESC  229188 non-null  object 
dtypes: float64(2), int64(1), object(3)
memory usage: 10.5+ MB


UNITID  OPEID6                    INSTNM  CIPCODE  CREDLEV  \
0  100654.0  1002.0  Alabama A & M University    100.0        3   
1  100654.0  1002.0  Alabama A & M University    101.0        3   
2  100654.0  1002.0  Alabama A & M University    109.0        3   
3  100654.0  1002.0  Alabama A & M University    110.0        3   
4  100654.0  1002.0  Alabama A & M University    110.0        5   

            CREDDESC  
0  Bachelor's Degree  
1  Bachelor's Degree  
2  Bachelor's Degree  
3  Bachelor's Degree  
4    Master's Degree

<div style="background-color: #f5f5f5; padding: 10px; border-radius: 5px; border: 3px solid #9101EC;">
  <strong> Checking to see what I have </strong>
</div>

In [94]:
#lists all databases (in file directory--not just connected)
# List all .db or .sqlite files in current directory

import os

db_files = [f for f in os.listdir('.') if f.endswith(('.db', '.sqlite'))]
print("📁 SQLite database files found:")
print(db_files)


📁 SQLite database files found:
['tuition.db', 'studyareas.db', 'your_database.db', 'collegedata.db', 'studayareas.db']


In [127]:
studyareasdf.head()

UNITID  OPEID6                    INSTNM  CIPCODE  CREDLEV  \
0  100654.0  1002.0  Alabama A & M University    100.0        3   
1  100654.0  1002.0  Alabama A & M University    101.0        3   
2  100654.0  1002.0  Alabama A & M University    109.0        3   
3  100654.0  1002.0  Alabama A & M University    110.0        3   
4  100654.0  1002.0  Alabama A & M University    110.0        5   

            CREDDESC  
0  Bachelor's Degree  
1  Bachelor's Degree  
2  Bachelor's Degree  
3  Bachelor's Degree  
4    Master's Degree

In [129]:
studyareasdf.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 229188 entries, 0 to 229187
Data columns (total 6 columns):
 #   Column    Non-Null Count   Dtype  
---  ------    --------------   -----  
 0   UNITID    229188 non-null  object 
 1   OPEID6    229188 non-null  float64
 2   INSTNM    229188 non-null  object 
 3   CIPCODE   229188 non-null  float64
 4   CREDLEV   229188 non-null  int64  
 5   CREDDESC  229188 non-null  object 
dtypes: float64(2), int64(1), object(3)
memory usage: 10.5+ MB


In [ ]:
# Convert to numeric (will convert invalid to NaN)
tuitiondf['Unit_ID'] = pd.to_numeric(tuitiondf['Unit_ID'], errors='coerce')

In [154]:
# Convert to numeric and coerce bad values to NaN
studyareasdf['UNITID'] = pd.to_numeric(studyareasdf['UNITID'], errors='coerce')

# Fill NaNs (use a sensible default like 0 or -1)
studyareasdf['UNITID'] = studyareasdf['UNITID'].fillna(0)

# Convert to integer type
studyareasdf['UNITID'] = studyareasdf['UNITID'].astype('int32')


In [156]:
# Convert float (except for money) to integer type
studyareasdf['OPEID6'] = studyareasdf['OPEID6'].astype('int32')
studyareasdf['CIPCODE'] = studyareasdf['CIPCODE'].astype('int32')
studyareasdf['CREDLEV'] = studyareasdf['CREDLEV'].astype('int32')
studyareasdf.head()

UNITID  OPEID6                    INSTNM  CIPCODE  CREDLEV  \
0  100654    1002  Alabama A & M University      100        3   
1  100654    1002  Alabama A & M University      101        3   
2  100654    1002  Alabama A & M University      109        3   
3  100654    1002  Alabama A & M University      110        3   
4  100654    1002  Alabama A & M University      110        5   

            CREDDESC  
0  Bachelor's Degree  
1  Bachelor's Degree  
2  Bachelor's Degree  
3  Bachelor's Degree  
4    Master's Degree

In [ ]:
'''
UNITID    #needs to be numeric
 1   OPEID6    229188 non-null  float64 stay
 2   INSTNM    229188 non-null  object --> string
 3   CIPCODE   229188 non-null  float64
 4   CREDLEV   229188 non-null  int64  --> int8
 5   CREDDESC ---> string
 '''

<div style="background-color: #f5f5f5; padding: 10px; border-radius: 5px; border: 3px solid #ff46A2;">
  <strong> College Data </strong>
</div>

In [100]:
conn = sqlite3.connect('collegedata.db')
collegedatadf = pd.read_sql_query("SELECT * FROM collegedata", conn)
collegedatadf.info()
collegedatadf.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12298 entries, 0 to 12297
Data columns (total 15 columns):
 #   Column                                       Non-Null Count  Dtype 
---  ------                                       --------------  ----- 
 0   School Name                                  12298 non-null  object
 1   Address                                      12298 non-null  object
 2   City                                         12298 non-null  object
 3   State                                        12298 non-null  object
 4   Zipcode                                      12298 non-null  object
 5   Type                                         12298 non-null  object
 6   Degrees Offered                              12298 non-null  object
 7   Campus Setting                               12298 non-null  object
 8   Campus Housing                               12298 non-null  object
 9   Student Population                           12298 non-null  object
 10  Undergradu

School Name                           Address         City  \
0               ASA College               !51 Lawrence Street     Brooklyn   
1      ATA Career Education  7351 Spring Hill Drive, Suite 11  Spring Hill   
2               ATA College     10200 Linn Station Rd Ste 125   Louisville   
3  ATA College - Cincinnati     225 Pictoria Drive, Suite 200   Cincinnati   
4    Aaniiih Nakoda College       269 Blackfeet Avenue Agency       Harlem   

  State     Zipcode                              Type  \
0  null  11201-9805                Four or more years   
1  null       34606  At least 2 but less than 4 years   
2  null       40223  At least 2 but less than 4 years   
3  null       45246  At least 2 but less than 4 years   
4  null       59526  At least 2 but less than 4 years   

                                     Degrees Offered Campus Setting  \
0  One but less than two years certificate , Asso...           City   
1  One but less than two years certificate , Asso...         Suburb   
2  One but less than two years certificate , Asso...         Suburb   
3  One but less than two years certificate , Asso...         Suburb   
4  Less than one year certificate , One but less ...          Rural   

  Campus Housing Student Population Undergraduate Students  \
0            Yes               4358                   4358   
1             No                289                    289   
2             No                332                    332   
3             No                250                    250   
4             No                131                    131   

       Public-Private Published In-state Tuition and Fees ($)  \
0  Private For-Profit                                   12728   
1  Private For-Profit                                   12959   
2  Private For-Profit                                   13025   
3  Private For-Profit                                   13295   
4              Public                                    2410   

  Published Out-of-state Tuition and Fees ($)  \
0                                       12728   
1                                       12959   
2                                       13025   
3                                       13295   
4                                        2410   

                Profile Link to College Navigator  
0  http://nces.ed.gov/collegenavigator/?id=404994  
1  http://nces.ed.gov/collegenavigator/?id=446127  
2  http://nces.ed.gov/collegenavigator/?id=447935  
3  http://nces.ed.gov/collegenavigator/?id=452373  
4  http://nces.ed.gov/collegenavigator/?id=180203

In [163]:
#converting data types
collegedatadf["School Name"] = collegedatadf["School Name"].astype("string")
collegedatadf["City"] = collegedatadf["City"].astype("string")
collegedatadf["State"] = collegedatadf["State"].astype("string")
collegedatadf["Campus Setting"] = collegedatadf["Campus Setting"].astype("string")
collegedatadf["Campus Housing"] = collegedatadf["Campus Housing"].astype("string")
collegedatadf["Published In-state Tuition and Fees ($)"] = collegedatadf["Published In-state Tuition and Fees ($)"].astype("int64")
collegedatadf["Published Out-of-state Tuition and Fees ($)"] = collegedatadf["Published Out-of-state Tuition and Fees ($)"].astype("int64")
collegedatadf.head()


ValueError: invalid literal for int() with base 10: 'null'

In [73]:
# Convert text columns safely to string dtype
collegedatadf["School Name"] = collegedatadf["School Name"].astype("string")
collegedatadf["City"] = collegedatadf["City"].astype("string")
collegedatadf["State"] = collegedatadf["State"].astype("string")
collegedatadf["Campus Setting"] = collegedatadf["Campus Setting"].astype("string")
collegedatadf["Campus Housing"] = collegedatadf["Campus Housing"].astype("string")

# Clean and convert tuition columns
for col in ["Published In-state Tuition and Fees ($)", "Published Out-of-state Tuition and Fees ($)"]:
    collegedatadf[col] = (
        collegedatadf[col]
        .astype(str)
        .str.replace(",", "", regex=False)
        .str.strip()
    )
    collegedatadf[col] = pd.to_numeric(collegedatadf[col], errors="coerce").fillna(0).astype("int64")

# Preview the result
collegedatadf.head()

NameError: name 'collegedatadf' is not defined

In [171]:
# Select only object/string columns
stringcol1 = collegedatadf.select_dtypes(include="object").columns
stringcol2 = collegedatadf.select_dtypes(include="string").columns

# Check for rows where stripping changes the value
mask1 = collegedatadf[stringcol1].apply(lambda col: col != col.str.strip())
mask2 = collegedatadf[stringcol2].apply(lambda col: col != col.str.strip())

# Show which rows and columns have leading/trailing spaces
rowswithspaces1 = mask1.any(axis=1)
rowswithspaces2 = mask2.any(axis=1)
collegedatadf[rowswithspaces1]
collegedatadf[rowswithspaces2]


Empty DataFrame
Columns: [School Name, Address, City, State, Zipcode, Type, Degrees Offered, Campus Setting, Campus Housing, Student Population, Undergraduate Students, Public-Private, Published In-state Tuition and Fees ($), Published Out-of-state Tuition and Fees ($), Profile Link to College Navigator]
Index: []

In [ ]:
-----------------------------------------------------------------------------------------------------------------------------------

In [ ]:
# 1. After thinking about the data model I want, I need to bring in field of study (hereafter called study area) data. 
# 2. If not in a table or database, then put in one.  
# 3. I need to consolidate the tables into one database. 

In [6]:
import sqlite3

# Connect to your SQLite database
conn = sqlite3.connect('collegedata.db')  # Replace with your database file name
cursor = conn.cursor()  # ✅ Define the cursor before using it

# Now you can safely run the query
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
tables = cursor.fetchall()

# Print all table names
print("Tables in database:", tables)

# Always good practice to close the connection when done
conn.close()


Tables in database: [('studyareas',), ('collegedata',), ('collegedata_new',)]


In [12]:
#import studyareas data
import sqlite3
import pandas as pd

import sqlite3
import pandas as pd

# Step 1: Connect to the database
conn = sqlite3.connect('collegedata.db')  # Replace with your .db file path

# Step 2: Read the specific table into a DataFrame
studyareas = 'studyareas'  # Replace with your table name
studyareasdf = pd.read_sql_query(f"SELECT * FROM {studyareas}", conn)

# Step 3: View the data
print(studyareasdf.head())


Empty DataFrame
Columns: [School, Address, City, State, Zipcode, Type, Degrees, Campus Setting, Campus Housing, Student, Undergraduate, Public-Private, Published In-state Tuition and Fees($), Published Out-of-state Tuition and Fees($)]
Index: []


In [6]:
import os
print(os.path.exists('/Users/Public/Most-Recent-Cohorts-Field-of-Study-2.csv'))


True


In [3]:
import pandas as pd
file_path = '/Users/Public/Most-Recent-Cohorts-Field-of-Study-2.csv'
fieldofstudy = pd.read_csv(file_path)
fieldofstudy.head()


UNITID  OPEID6                    INSTNM CONTROL  MAIN  CIPCODE  \
0  100654.0    1002  Alabama A & M University  Public     1      100   
1  100654.0    1002  Alabama A & M University  Public     1      101   
2  100654.0    1002  Alabama A & M University  Public     1      109   
3  100654.0    1002  Alabama A & M University  Public     1      110   
4  100654.0    1002  Alabama A & M University  Public     1      110   

                                 CIPDESC  CREDLEV           CREDDESC  \
0                  Agriculture, General.        3  Bachelor's Degree   
1  Agricultural Business and Management.        3  Bachelor's Degree   
2                       Animal Sciences.        3  Bachelor's Degree   
3           Food Science and Technology.        3  Bachelor's Degree   
4           Food Science and Technology.        5    Master's Degree   

   IPEDSCOUNT1  ...  EARN_COUNT_PELL_WNE_5YR EARN_PELL_WNE_MDN_5YR  \
0          NaN  ...                       PS                    PS   
1          NaN  ...                       PS                    PS   
2          3.0  ...                       PS                    PS   
3          7.0  ...                       PS                    PS   
4          4.0  ...                       PS                    PS   

  EARN_COUNT_NOPELL_WNE_5YR EARN_NOPELL_WNE_MDN_5YR EARN_COUNT_MALE_WNE_5YR  \
0                        PS                      PS                      PS   
1                        PS                      PS                      PS   
2                        PS                      PS                      PS   
3                        PS                      PS                      PS   
4                        PS                      PS                      PS   

  EARN_MALE_WNE_MDN_5YR EARN_COUNT_NOMALE_WNE_5YR EARN_NOMALE_WNE_MDN_5YR  \
0                    PS                        PS                      PS   
1                    PS                        PS                      PS   
2                    PS                        PS                      PS   
3                    PS                        PS                      PS   
4                    PS                        PS                      PS   

  EARN_COUNT_HIGH_CRED_5YR EARN_IN_STATE_5YR  
0                       PS                PS  
1                       PS                PS  
2                       PS                PS  
3                       PS                PS  
4                       PS                PS  

[5 rows x 174 columns]

In [16]:
import pandas as pd
ncaapath = '/Users/Public/ncaa_all_divisions.csv'

In [24]:
#Basic Profile data
import pandas as pd

# Load the CSV file into a DataFrame
ncaadf = pd.read_csv(ncaapath)

# Show basic profile information about the DataFrame
ncaadf.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 948 entries, 0 to 947
Data columns (total 36 columns):
 #   Column                                         Non-Null Count  Dtype  
---  ------                                         --------------  -----  
 0   0                                              1 non-null      object 
 1   1                                              1 non-null      object 
 2   2                                              1 non-null      object 
 3   NCAA Division                                  948 non-null    object 
 4   School                                         914 non-null    object 
 5   Nickname                                       913 non-null    object 
 6   City                                           741 non-null    object 
 7   State/ Province                                293 non-null    object 
 8   Enrollment                                     306 non-null    object 
 9   Conference                                     922 non

In [28]:
# Select specific columns
ncaasubset = ncaadf[['NCAA Division', 'School', 'Nickname', 'City', 'State', 'Conference']]


In [30]:
ncaasubset.head()

NCAA Division                               School       Nickname  \
0    Division I                                  NaN            NaN   
1   Division II         Academy of Art University[a]  Urban Knights   
2   Division II               Adams State University      Grizzlies   
3   Division II                   Adelphi University       Panthers   
4   Division II  University of Alabama in Huntsville       Chargers   

            City State                          Conference  
0            NaN   NaN                                 NaN  
1  San Francisco   NaN             Pacific West Conference  
2        Alamosa   NaN  Rocky Mountain Athletic Conference  
3    Garden City   NaN             Northeast-10 Conference  
4     Huntsville   NaN               Gulf South Conference

In [32]:
# Remove row with index 5
ncaasubset = ncaasubset.drop(0)
ncaasubset.head()


NCAA Division                               School       Nickname  \
1   Division II         Academy of Art University[a]  Urban Knights   
2   Division II               Adams State University      Grizzlies   
3   Division II                   Adelphi University       Panthers   
4   Division II  University of Alabama in Huntsville       Chargers   
5   Division II       University of Alaska Anchorage      Seawolves   

            City State                           Conference  
1  San Francisco   NaN              Pacific West Conference  
2        Alamosa   NaN   Rocky Mountain Athletic Conference  
3    Garden City   NaN              Northeast-10 Conference  
4     Huntsville   NaN                Gulf South Conference  
5      Anchorage   NaN  Great Northwest Athletic Conference

In [34]:
##I have the data. Now I need to put all of the tables in one database.

import os

db_files = [f for f in os.listdir('.') if f.endswith(('.db', '.sqlite'))]
print("📁 SQLite database files found:")
print(db_files)

📁 SQLite database files found:
['tuition.db', 'studyareas.db', 'your_database.db', 'collegedata.db', 'studayareas.db']


In [36]:
#List the tables for each database
import sqlite3

# Connect to the SQLite database file
conn = sqlite3.connect('your_database_file.db')  # replace with your .db file path
cursor = conn.cursor()

# List all tables
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
tables = cursor.fetchall()

# Print table names
for table in tables:
    print(table[0])


In [40]:
# Connect to the SQLite database file
conn = sqlite3.connect('tution.db')  # replace with your .db file path
cursor = conn.cursor()

# List all tables
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
tuitiontables = cursor.fetchall()

# Print table names
for table in tuitiontables:
    print(table[0])

In [42]:
# Connect to the SQLite database file
conn = sqlite3.connect('studyareas.db')  # replace with your .db file path
cursor = conn.cursor()

# List all tables
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
studyareastables = cursor.fetchall()

# Print table names
for table in studyareastables:
    print(table[0])

studyareas


In [44]:
# Connect to the SQLite database file
conn = sqlite3.connect('collegedata.db')  # replace with your .db file path
cursor = conn.cursor()

# List all tables
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
collegedatatables = cursor.fetchall()

# Print table names
for table in collegedatatables:
    print(table[0])

studyareas
collegedata
collegedata_new


In [46]:
# Connect to the SQLite database file
conn = sqlite3.connect('studayareas.db')  # replace with your .db file path
cursor = conn.cursor()

# List all tables
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
studyareastables = cursor.fetchall()

# Print table names
for table in studyareastables:
    print(table[0])

In [48]:
import sqlite3
import pandas as pd

# Connect to the source and destination databases
source_conn = sqlite3.connect('studyareas.db')
dest_conn = sqlite3.connect('collegedata.db')

# Step 1: List tables in source.db
source_cursor = source_conn.cursor()
source_cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
tables = source_cursor.fetchall()

# Step 2: Copy each table to destination.db
for table_name in tables:
    table = table_name[0]
    df = pd.read_sql_query(f"SELECT * FROM {table}", source_conn)
    df.to_sql(table, dest_conn, if_exists='replace', index=False)
    print(f"Copied table: {table}")

# Close connections
source_conn.close()
dest_conn.close()


Copied table: studyareas


In [50]:

# Connect to the source and destination databases
source_conn = sqlite3.connect('tuition.db')
dest_conn = sqlite3.connect('collegedata.db')

# Step 1: List tables in source.db
source_cursor = source_conn.cursor()
source_cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
tables = source_cursor.fetchall()

# Step 2: Copy each table to destination.db
for table_name in tables:
    table = table_name[0]
    df = pd.read_sql_query(f"SELECT * FROM {table}", source_conn)
    df.to_sql(table, dest_conn, if_exists='replace', index=False)
    print(f"Copied table: {table}")

# Close connections
source_conn.close()
dest_conn.close()

Copied table: tuition


In [68]:
import sqlite3
import pandas as pd

# Step 1: Read the CSV file into a DataFrame
csv_file = '/users/public/ncaa_all_divisions.csv'  # Replace with your actual file path
ncaadf = pd.read_csv(csv_file)

# Step 2: Connect to the existing database
conn = sqlite3.connect('collegedata.db')  # Replace with your actual DB path

# Step 3: Create a new table (or update an existing one)
df.to_sql('ncaa', conn, if_exists='replace', index=False)

# Options for if_exists:
# - 'replace' → drops and recreates the table
# - 'append'  → adds to the existing table
# - 'fail'    → errors if the table already exists

# Step 4: Close the connection
conn.close()

# Print table names
for table in collegedatatables:
    print(table[0])



studyareas
collegedata
collegedata_new


In [ ]:
#I keep trying to combine the tables into one database, but cannot get it to work. 